In [1]:
import requests
from bs4 import BeautifulSoup

race_id = '202106030811'
url = 'https://db.netkeiba.com/race/' +race_id
html = requests.get(url)
html.encoding = 'EUC-JP'
soup = BeautifulSoup(html.text, 'html.parser')

In [2]:
import re
# soupのメソッド名はfind_all、reのメソッド名はfindall
test = soup.find('table',attrs={'summary':'レース結果'}).find_all('a',attrs={'href':re.compile('^/horse')})

In [3]:
re.findall(r'\d+', test[0]['href'])

['2018105027']

In [4]:
horse_id_list = []
for a in test:
    horse_id = re.findall(r'\d+', a['href'])
    horse_id_list.append(horse_id[0])

In [5]:
horse_id_list

['2018105027',
 '2018103559',
 '2018104980',
 '2018105092',
 '2018105012',
 '2018105277',
 '2018104475',
 '2018105366',
 '2018104948',
 '2018105402',
 '2018104942',
 '2018100026',
 '2018105060',
 '2018100995',
 '2018104963',
 '2018101071']

In [8]:
import pandas as pd
import time
from tqdm.notebook import tqdm_notebook as tqdm

def scraping_race_result(id_list, pre_race_results={}):
    race_results = pre_race_results
    
    for race_id in tqdm(id_list):
        if race_id in pre_race_results.keys():
            continue
        try:
            time.sleep(0.1)
            url='https://db.netkeiba.com/race/' + race_id
            df = pd.read_html(url)[0]
            #horse_idとjockey_idを入れる
            html = requests.get(url)
            html.encoding = 'EUC-JP'
            soup = BeautifulSoup(html.text, 'html.parser')
            
            horse_id_list = []
            horse_a_list = soup.find('table',attrs={'summary':'レース結果'})\
                .find_all('a',attrs={'href':re.compile('^/horse')})
            for a in horse_a_list:
                horse_id = re.findall(r'\d+', a['href'])
                horse_id_list.append(horse_id[0])
                
            jockey_id_list = []
            jockey_a_list = soup.find('table',attrs={'summary':'レース結果'})\
                .find_all('a',attrs={'href':re.compile('^/jockey')})
            for a in horse_a_list:
                jockey_id = re.findall(r'\d+', a['href'])
                jockey_id_list.append(jockey_id[0])
                
            df['horse_id'] = horse_id_list
            df['jockey_id'] = jockey_id_list
            
            race_results[race_id] = df
        except IndexError:
            continue
        except:
            break
    return race_results

In [8]:
scraping_race_result(['202106030811'])

{'202106030811':     着順  枠番  馬番         馬名  性齢  斤量    騎手     タイム     着差     単勝  人気       馬体重  \
 0    1   4   7    エフフォーリア  牡3  57  横山武史  2:00.6    NaN    3.7   2  504(-10)   
 1    2   7  13   タイトルホルダー  牡3  57  田辺裕信  2:01.1      3   17.0   8   462(-4)   
 2    3   2   3  ステラヴェローチェ  牡3  57  吉田隼人  2:01.1     クビ   14.3   6    500(0)   
 3    4   1   1   アドマイヤハダル  牡3  57  ルメール  2:01.2     クビ    8.8   3   482(-2)   
 4    5   3   6    ヨーホーレイク  牡3  57  岩田望来  2:01.2     クビ   21.5  11   504(-2)   
 5    6   8  15     グラティアス  牡3  57  Ｍ．デム  2:01.3    1/2   15.7   7   500(+2)   
 6    7   6  11  ディープモンスター  牡3  57  戸崎圭太  2:01.4     クビ   19.6  10   444(-8)   
 7    8   8  16   レッドベルオーブ  牡3  57  福永祐一  2:01.8  2.1/2   18.8   9   478(+2)   
 8    9   3   5  ヴィクティファルス  牡3  57  池添謙一  2:02.1  1.3/4   10.1   4   478(-2)   
 9   10   2   4  イルーシヴパンサー  牡3  57  大野拓弥  2:02.2    3/4  179.9  15   472(+2)   
 10  11   5  10  シュヴァリエローズ  牡3  57  三浦皇成  2:02.4  1.1/4  109.1  13   440(-4)   
 11  12   6  12  ワールドリバイ

In [7]:
race_id_list = pd.read_pickle('result_addinfo.pickle').index.unique()

In [9]:
result_new = scraping_race_result(race_id_list)

In [29]:
result_new

{'202001010101':    着順  枠番  馬番         馬名  性齢  斤量    騎手     タイム     着差    単勝  人気      馬体重  \
 0   1   6   6     ウインルーア  牝2  54  横山武史  1:49.7    NaN  16.0   3  438(+4)   
 1   2   2   2     アークライト  牡2  54  ルメール  1:50.0  1.3/4   1.9   2   510(0)   
 2   3   3   3  ギャラントウォリア  牡2  54  池添謙一  1:50.1    1/2   1.8   1  482(-6)   
 3   4   1   1     ジュンブーケ  牝2  52  亀田温心  1:50.5  2.1/2  22.2   4   442(0)   
 4   5   4   4    キタノマンゲツ  牡2  54  藤岡康太  1:51.0      3  55.7   5  426(-8)   
 5   6   5   5     アイフレンズ  牝2  54   黛弘人  1:52.7      大  73.9   6  426(-2)   
 
         調教師    horse_id   jockey_id  
 0  [東] 青木孝文  2018101626  2018101626  
 1  [東] 藤沢和雄  2018105193  2018105193  
 2   [西] 平田修  2018104800  2018104800  
 3   [西] 森秀行  2018102410  2018102410  
 4  [西] 中尾秀正  2018100828  2018100828  
 5  [東] 中野栄治  2018106434  2018106434  ,
 '202001010102':     着順  枠番  馬番         馬名  性齢  斤量    騎手     タイム     着差     単勝  人気      馬体重  \
 0    1   3   4    バトルピアサー  牝3  54  川島信二  1:46.2    NaN    2.7   1  406(-2

In [10]:
test = result_new.copy()

for key in test.keys():
    test[key].index = [key]*len(test[key])
    
result = pd.concat([test[key] for key in test.keys()],sort=False)

pd.DataFrame(result)

着順  枠番  馬番         馬名  性齢    斤量    騎手     タイム     着差    単勝  \
202001010101   1   6   6     ウインルーア  牝2  54.0  横山武史  1:49.7    NaN    16   
202001010101   2   2   2     アークライト  牡2  54.0  ルメール  1:50.0  1.3/4   1.9   
202001010101   3   3   3  ギャラントウォリア  牡2  54.0  池添謙一  1:50.1    1/2   1.8   
202001010101   4   1   1     ジュンブーケ  牝2  52.0  亀田温心  1:50.5  2.1/2  22.2   
202001010101   5   4   4    キタノマンゲツ  牡2  54.0  藤岡康太  1:51.0      3  55.7   
...           ..  ..  ..        ...  ..   ...   ...     ...    ...   ...   
202010020812  11   1   1       キスラー  牡4  57.0    武豊  1:45.5      1   6.5   
202010020812  12   8  14    ポンペイワーム  牡4  57.0   浜中俊  1:45.6     クビ  19.8   
202010020812  13   8  15  アルマトップエンド  牡5  57.0  国分恭介  1:45.9  1.3/4    75   
202010020812  14   2   3      ノイーヴァ  牝4  55.0  太宰啓介  1:46.7      5  46.1   
202010020812  15   7  13   ナイトオブレディ  牝3  52.0  川又賢治  1:47.5      5  24.7   

                人気       馬体重       調教師    horse_id   jockey_id  
202001010101   3.0   438(+4)  [東] 青木孝文  2018101626  2018101626  
202001010101   2.0    510(0)  [東] 藤沢和雄  2018105193  2018105193  
202001010101   1.0   482(-6)   [西] 平田修  2018104800  2018104800  
202001010101   4.0    442(0)   [西] 森秀行  2018102410  2018102410  
202001010101   5.0   426(-8)  [西] 中尾秀正  2018100828  2018100828  
...            ...       ...       ...         ...         ...  
202010020812   4.0   476(-2)  [西] 池江泰寿  2016105042  2016105042  
202010020812   8.0   522(-8)   [西] 石坂正  2016110126  2016110126  
202010020812  14.0    510(0)  [西] 佐々木晶  2015102639  2015102639  
202010020812  10.0  488(-12)  [西] 安田翔伍  2016110067  2016110067  
202010020812   9.0   468(+2)  [西] 庄野靖志  2017105123  2017105123  

[43609 rows x 15 columns]

In [11]:
# 馬ごとのレース結果を取得

horse_id_list = result['horse_id'].unique()

In [12]:
len(horse_id_list)

11389

In [13]:
def scraping_horse_result(id_list, pre_horse_results={}):
    horse_results = pre_horse_results #処理を途中で止めた後でそこから再開できるように
    
    for horse_id in tqdm(id_list):
        if horse_id in horse_results.keys():
            continue
        try:
            time.sleep(0.1)
            url='https://db.netkeiba.com/horse/' + horse_id
            df = pd.read_html(url)[3]
            horse_results[horse_id] = df
        except IndexError:
            continue
        except:
            break
    return horse_results

In [14]:
horse_result = scraping_horse_result(horse_id_list)

In [15]:
horse_result 

{'2018101626':            日付    開催 天気   R       レース名  映像  頭数  枠番  馬番   オッズ  ...   着差  ﾀｲﾑ指数  \
 0  2021/04/11  3中山6  晴   7    3歳1勝クラス NaN  10   1   1  52.9  ...  0.8     **   
 1  2021/03/27  3中山1  晴   6    3歳1勝クラス NaN   8   8   8  72.1  ...  1.2     **   
 2  2021/03/13  2中山5  雨   7    3歳1勝クラス NaN  11   6   7  99.2  ...  2.9     **   
 3  2020/10/03  4中山8  曇   9    芙蓉S(OP) NaN   9   1   1  35.0  ...  1.8     **   
 4  2020/09/05  2札幌7  晴  11  札幌2歳S(G3) NaN  14   6   9  10.7  ...  1.3     **   
 5  2020/07/25  1札幌1  曇   1      2歳未勝利 NaN   6   6   6  16.0  ... -0.3     **   
 6  2020/06/13  1函館1  晴   6       2歳新馬 NaN  11   5   5   9.5  ...  1.5     **   
 
          通過        ペース    上り      馬体重 厩舎ｺﾒﾝﾄ  備考   勝ち馬(2着馬)     賞金  
 0   5-6-6-5  38.0-34.7  34.6  450(+2)    NaN NaN    ミヤビハイディ    NaN  
 1   8-8-8-8  36.3-36.6  36.3  448(+4)    NaN NaN   スペシャルドラマ    NaN  
 2   9-9-7-8  37.5-38.2  40.5   444(0)    NaN NaN  ヴァイスメテオール    NaN  
 3   7-7-9-9  36.2-35.5  36.2  444(+8)    NaN NaN  ランドオブ

In [17]:
test2 = horse_result.copy()

for key in test2.keys():
    test2[key].index = [key]*len(test2[key])
    
result2 = pd.concat([test2[key] for key in test2.keys()],sort=False)

pd.DataFrame(result2)

日付    開催 天気     R       レース名  映像    頭数   枠番    馬番   オッズ  \
2018101626  2021/04/11  3中山6  晴   7.0    3歳1勝クラス NaN  10.0  1.0   1.0  52.9   
2018101626  2021/03/27  3中山1  晴   6.0    3歳1勝クラス NaN   8.0  8.0   8.0  72.1   
2018101626  2021/03/13  2中山5  雨   7.0    3歳1勝クラス NaN  11.0  6.0   7.0  99.2   
2018101626  2020/10/03  4中山8  曇   9.0    芙蓉S(OP) NaN   9.0  1.0   1.0  35.0   
2018101626  2020/09/05  2札幌7  晴  11.0  札幌2歳S(G3) NaN  14.0  6.0   9.0  10.7   
...                ...   ... ..   ...        ...  ..   ...  ...   ...   ...   
2014102720  2017/02/19  2京都8  晴   2.0      3歳未勝利 NaN  16.0  8.0  16.0   9.2   
2014102720  2017/02/12  2京都6  晴   5.0      3歳未勝利 NaN  16.0  5.0  10.0  33.3   
2014102720  2017/01/21  1京都6  晴   5.0      3歳未勝利 NaN  14.0  5.0   8.0   8.4   
2014102720  2016/12/25  5阪神9  晴   4.0      2歳未勝利 NaN  15.0  1.0   1.0  10.4   
2014102720  2016/12/11  4中京4  晴   5.0       2歳新馬 NaN   9.0  5.0   5.0  30.2   

            ...  ﾀｲﾑ指数        通過        ペース    上り      馬体重 厩舎ｺﾒﾝﾄ  備考  \
2018101626  ...     **   5-6-6-5  38.0-34.7  34.6  450(+2)    NaN NaN   
2018101626  ...     **   8-8-8-8  36.3-36.6  36.3  448(+4)    NaN NaN   
2018101626  ...     **   9-9-7-8  37.5-38.2  40.5   444(0)    NaN NaN   
2018101626  ...     **   7-7-9-9  36.2-35.5  36.2  444(+8)    NaN NaN   
2018101626  ...     **  6-6-5-10  35.0-36.9  37.8  436(-2)    NaN NaN   
...         ...    ...       ...        ...   ...      ...    ...  ..   
2014102720  ...     **       2-2  35.2-38.6  38.8  480(-4)    NaN NaN   
2014102720  ...     **       1-1  35.0-37.0  38.6   484(0)    NaN NaN   
2014102720  ...     **   2-2-2-2  36.5-36.0  38.3  484(-2)    NaN NaN   
2014102720  ...     **   1-1-1-1  37.4-36.8  37.2  486(-4)    NaN NaN   
2014102720  ...     **   1-1-1-1  38.8-34.5  34.9   490(0)    NaN NaN   

             勝ち馬(2着馬)     賞金  受賞歴  
2018101626    ミヤビハイディ    NaN  NaN  
2018101626   スペシャルドラマ    NaN  NaN  
2018101626  ヴァイスメテオール    NaN  NaN  
2018101626  ランドオブリバティ    NaN  NaN  
2018101626        ソダシ    NaN  NaN  
...               ...    ...  ...  
2014102720  クリノアントニヌス  130.0  NaN  
2014102720    ゴールドハット    NaN  NaN  
2014102720  エスピリトゥオーゾ    NaN  NaN  
2014102720  ウィズワンアセント    NaN  NaN  
2014102720   ダノンキングダム  280.0  NaN  

[171762 rows x 29 columns]

In [18]:
result2.to_pickle('horse_data.pickle')

In [20]:
result.to_pickle('result_new.pickle')

In [118]:
class HorseResults:
    def __init__(self, horse_results):
        self.horse_results = horse_results[['日付','R','賞金']]
        self.preprocessing()
        self.horse_results.rename(columns={'着順':'着順_ave','賞金':'賞金_ave'}, inplace=True)
        
    def preprocessing(self): #特に引数がない場合はselfのみ
        result = self.horse_results.copy()
#         #着順の0-9以外の文字を含むデータを除く
#         result = result[-result["R"].astype(str).str.contains("\D")] 
        result["着順"] = result["R"].astype(float)
        result["賞金"] = result["賞金"].astype(float)
        result["日付"] = pd.to_datetime(result["日付"])
        result.drop(["R"],axis=1, inplace=True)
                    
        self.horse_results = result
        
    def average(self, horse_id_list, date):
        target_df = self.horse_results.loc[horse_id_list]
        return target_df[target_df['日付'] < date].groupby(level=0)[['着順_ave','賞金_ave']].mean()
    
    def merge(self, results, date):
        df = results[results['date'] < date]
        horse_id_list = df['horse_id']
        merged_df = df.merge(self.average(horse_id_list, date), left_on='horse_id', right_index=True, how='left')
        return merged_df
    
    def merge_all(self, results):
        date_list = results['date'].unique()
        #レース結果の同じ日付のかたまりごとに1行ずつhorse_idにひもづくその日付以前の戦績の平均を算出し（average）、
        # レース結果のかたまりにマージする(merge)という意味
        merged_df = pd.concat([self.merge(results, date) for date in tqdm(date_list)]) 
        return merged_df

In [119]:
hr = HorseResults(result2)

In [48]:
def preprocessing(kekka):
    result = kekka.copy()
    #着順の0-9以外の文字を含むデータを除く
    result = result[-result["着順"].astype(str).str.contains("\D")] 
    result["着順"] = result["着順"].astype(int)
    #性齢を性と齢に分ける
    result["性"] = result["性齢"].map(lambda x: str(x)[0])
    result["齢"] = result["性齢"].map(lambda x: str(x)[1:]).astype(int)
    #馬体重を体重と体重増減に分ける
    result["体重"] = result["馬体重"].str.split('(',expand=True)[0].astype(int)
    result["体重増減"] = result["馬体重"].str.split('(',expand=True)[1].str[:-1].astype(int)
    
    result["単勝"] = result["単勝"].astype(float)
    result.drop(['性齢','馬体重','タイム','着差','調教師'],axis=1,inplace=True)
    
    result_addinfo['course_len'] = result_addinfo['course_len'].astype(int)
    result['date'] = pd.to_datetime(result['date'], format='%Y年%m月%d日')
    return result

In [44]:
result

着順  枠番  馬番         馬名  性齢    斤量    騎手     タイム     着差    単勝  \
202001010101   1   6   6     ウインルーア  牝2  54.0  横山武史  1:49.7    NaN    16   
202001010101   2   2   2     アークライト  牡2  54.0  ルメール  1:50.0  1.3/4   1.9   
202001010101   3   3   3  ギャラントウォリア  牡2  54.0  池添謙一  1:50.1    1/2   1.8   
202001010101   4   1   1     ジュンブーケ  牝2  52.0  亀田温心  1:50.5  2.1/2  22.2   
202001010101   5   4   4    キタノマンゲツ  牡2  54.0  藤岡康太  1:51.0      3  55.7   
...           ..  ..  ..        ...  ..   ...   ...     ...    ...   ...   
202010020812  11   1   1       キスラー  牡4  57.0    武豊  1:45.5      1   6.5   
202010020812  12   8  14    ポンペイワーム  牡4  57.0   浜中俊  1:45.6     クビ  19.8   
202010020812  13   8  15  アルマトップエンド  牡5  57.0  国分恭介  1:45.9  1.3/4    75   
202010020812  14   2   3      ノイーヴァ  牝4  55.0  太宰啓介  1:46.7      5  46.1   
202010020812  15   7  13   ナイトオブレディ  牝3  52.0  川又賢治  1:47.5      5  24.7   

                人気       馬体重       調教師    horse_id   jockey_id  
202001010101   3.0   438(+4)  [東] 青木孝文  2018101626  2018101626  
202001010101   2.0    510(0)  [東] 藤沢和雄  2018105193  2018105193  
202001010101   1.0   482(-6)   [西] 平田修  2018104800  2018104800  
202001010101   4.0    442(0)   [西] 森秀行  2018102410  2018102410  
202001010101   5.0   426(-8)  [西] 中尾秀正  2018100828  2018100828  
...            ...       ...       ...         ...         ...  
202010020812   4.0   476(-2)  [西] 池江泰寿  2016105042  2016105042  
202010020812   8.0   522(-8)   [西] 石坂正  2016110126  2016110126  
202010020812  14.0    510(0)  [西] 佐々木晶  2015102639  2015102639  
202010020812  10.0  488(-12)  [西] 安田翔伍  2016110067  2016110067  
202010020812   9.0   468(+2)  [西] 庄野靖志  2017105123  2017105123  

[43609 rows x 15 columns]

In [45]:
race_infos = pd.read_pickle('race_infos.pickle')

In [46]:
result_addinfo = result.merge(race_infos, left_index=True, right_index=True, how='inner')

In [49]:
result_p = preprocessing(result_addinfo)
result_p

着順  枠番  馬番         馬名    斤量    騎手    単勝    人気    horse_id  \
202001010101   1   6   6     ウインルーア  54.0  横山武史  16.0   3.0  2018101626   
202001010101   2   2   2     アークライト  54.0  ルメール   1.9   2.0  2018105193   
202001010101   3   3   3  ギャラントウォリア  54.0  池添謙一   1.8   1.0  2018104800   
202001010101   4   1   1     ジュンブーケ  52.0  亀田温心  22.2   4.0  2018102410   
202001010101   5   4   4    キタノマンゲツ  54.0  藤岡康太  55.7   5.0  2018100828   
...           ..  ..  ..        ...   ...   ...   ...   ...         ...   
202010020812  11   1   1       キスラー  57.0    武豊   6.5   4.0  2016105042   
202010020812  12   8  14    ポンペイワーム  57.0   浜中俊  19.8   8.0  2016110126   
202010020812  13   8  15  アルマトップエンド  57.0  国分恭介  75.0  14.0  2015102639   
202010020812  14   2   3      ノイーヴァ  55.0  太宰啓介  46.1  10.0  2016110067   
202010020812  15   7  13   ナイトオブレディ  52.0  川又賢治  24.7   9.0  2017105123   

               jockey_id course_len weather race_type ground_state       date  \
202001010101  2018101626       1800       曇         芝            良 2020-07-25   
202001010101  2018105193       1800       曇         芝            良 2020-07-25   
202001010101  2018104800       1800       曇         芝            良 2020-07-25   
202001010101  2018102410       1800       曇         芝            良 2020-07-25   
202001010101  2018100828       1800       曇         芝            良 2020-07-25   
...                  ...        ...     ...       ...          ...        ...   
202010020812  2016105042       1700       雨       ダート            重 2020-09-06   
202010020812  2016110126       1700       雨       ダート            重 2020-09-06   
202010020812  2015102639       1700       雨       ダート            重 2020-09-06   
202010020812  2016110067       1700       雨       ダート            重 2020-09-06   
202010020812  2017105123       1700       雨       ダート            重 2020-09-06   

              性  齢   体重  体重増減  
202001010101  牝  2  438     4  
202001010101  牡  2  510     0  
202001010101  牡  2  482    -6  
202001010101  牝  2  442     0  
202001010101  牡  2  426    -8  
...          .. ..  ...   ...  
202010020812  牡  4  476    -2  
202010020812  牡  4  522    -8  
202010020812  牡  5  510     0  
202010020812  牝  4  488   -12  
202010020812  牝  3  468     2  

[43239 rows x 19 columns]

In [103]:
sample_date = '2020-09-06'

#horse_resultを参照してhorse_idをキーにして馬の戦績をマージする（ただしレースの日付より前の戦績のみ）
target_df = hr.horse_results.loc[horse_id_list]
target_df[target_df['日付'] < sample_date].groupby(level=0)[['着順','賞金']].mean()

着順          賞金
2009100502   6.950000  325.421739
2009102606  10.295082  652.691304
2009103405   8.710000  294.222222
2010100035  10.372093  950.084211
2010100690  10.431373  958.556000
...               ...         ...
2018110102   2.666667  155.000000
2018110107   5.000000         NaN
2018110118   5.000000  700.000000
2018110127   5.000000  180.000000
2018110133   5.000000   70.000000

[9508 rows x 2 columns]

In [110]:
#これをマージする
hr.average(horse_id_list, sample_date)

着順          賞金
2009100502   6.950000  325.421739
2009102606  10.295082  652.691304
2009103405   8.710000  294.222222
2010100035  10.372093  950.084211
2010100690  10.431373  958.556000
...               ...         ...
2018110102   2.666667  155.000000
2018110107   5.000000         NaN
2018110118   5.000000  700.000000
2018110127   5.000000  180.000000
2018110133   5.000000   70.000000

[9508 rows x 2 columns]

In [120]:
merged_results = hr.merge_all(result_p)

In [121]:
merged_results.to_pickle("merged_results.pickle")